In [56]:
import pandas as pd
import math
from tqdm import tqdm


# CS Rankings Author info

Taken from https://github.com/emeryberger/CSrankings/tree/gh-pages which is the repo behind https://csrankings.org 

Run `make generated-author-info.csv` which should make the csv. Each row contains the score for every author, year, and conference combination. This means that there are multiple rows for each professor.

# CS Professors

Taken from https://drafty.cs.brown.edu/csprofessors but they hide the data. So, after reading source code, exploit a [thing they left in](https://github.com/brownhci/drafty/blob/212bd995c857a34c74c7a71d67e1556c1ca7ea97/backend/src/controllers/datasharing.ts#L31) during development and use https://drafty.cs.brown.edu/data/csv/csprofessors/csprofessors_93318b344889ccef41d46b5f83d63de5 

# Placement Rank

Taken from https://drafty.cs.brown.edu/csopenrankings/placement-rank.html which is just copy and paste (and `M-x query-replace <tab> ,`). I think I could have done this myself, but why do that when someone else has already done the work. 

# Best Paper awards

A collection of best paper awards are listed on https://jeffhuang.com/best_paper_awards/

However, I needed to do some html parsing in order to get the data into a csv format. That is done in [another notebook](./best-paper.ipynb)

# Preferences
This is a list of conferences and areas and my interest in them. This is used in order to create weights. It is manually generated

# Universities
This is a list of north american universities and their aliases (e.g. NYU and New York University). It is manually generated (hence why it is only north american universities)

# [Data](https://store.sachiniyer.com/s/9NczHAmPJFiQgys)


In [152]:
dfcsrankings = pd.read_csv("data/generated-author-info.csv")
dfcsrankings.describe()

count  adjustedcount           year
count  199906.000000  199906.000000  199906.000000
mean        1.332511       0.384866    2012.689984
std         0.845756       0.281289       8.774593
min         1.000000       0.008696    1970.000000
25%         1.000000       0.200000    2008.000000
50%         1.000000       0.333330    2015.000000
75%         1.000000       0.500000    2020.000000
max        24.000000       4.977800    2023.000000

In [153]:
dfcsrankings.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 199906 entries, 0 to 199905
Data columns (total 6 columns):
 #   Column         Non-Null Count   Dtype  
---  ------         --------------   -----  
 0   name           199906 non-null  object 
 1   dept           199906 non-null  object 
 2   area           199906 non-null  object 
 3   count          199906 non-null  float64
 4   adjustedcount  199906 non-null  float64
 5   year           199906 non-null  int64  
dtypes: float64(2), int64(1), object(3)
memory usage: 9.2+ MB


In [155]:
dfcsrankings.sample(3)

name                         dept     area  count  \
134515   Pranjal Awasthi           Rutgers University     nips    1.0   
144619  Ronald A. Olsson  Univ. of California - Davis  oakland    1.0   
131224    Peter K. Allen          Columbia University     iros    1.0   

        adjustedcount  year  
134515        0.25000  2014  
144619        0.20000  1998  
131224        0.33333  2005

In [134]:
dfcsprofs = pd.read_csv("data/csprofessors.csv")
dfcsprofs.describe()

UniqueId     JoinYear
count  5630.000000  5512.000000
mean   3098.262877  2007.741473
std    1784.465144    11.730682
min       1.000000  1963.000000
25%    1569.250000  2001.000000
50%    3081.500000  2011.000000
75%    4623.750000  2017.000000
max    6212.000000  2024.000000

In [135]:
dfcsprofs.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5630 entries, 0 to 5629
Data columns (total 7 columns):
 #   Column      Non-Null Count  Dtype  
---  ------      --------------  -----  
 0   UniqueId    5630 non-null   int64  
 1   FullName    5629 non-null   object 
 2   University  5630 non-null   object 
 3   JoinYear    5512 non-null   float64
 4   SubField    5625 non-null   object 
 5   Bachelors   5331 non-null   object 
 6   Doctorate   5618 non-null   object 
dtypes: float64(1), int64(1), object(5)
memory usage: 308.0+ KB


In [156]:
dfcsprofs.sample(3)

UniqueId           FullName                          University  \
3536      3873  ThanhVu H. Nguyen      University of Nebraska-Lincoln   
2896      3180   Nikolaus Correll      University of Colorado Boulder   
2327      2567           Asanovic  University of California, Berkeley   

      JoinYear                 SubField                       Bachelors  \
3536    2017.0    Programming Languages   Pennsylvania State University   
2896    2009.0  Artificial Intelligence  Technical University of Munich   
2327    2007.0    Computer Architecture         University of Cambridge   

                                     Doctorate  
3536                  University of New Mexico  
2896  École polytechnique fédérale de Lausanne  
2327        University of California, Berkeley

In [138]:
dfplacement = pd.read_csv("data/placement-rank.csv", delimiter='|')
dfplacement.describe()

num        size   bachelors   doctorate  placementscore
count  183.000000  115.000000  168.000000  159.000000      183.000000
mean    92.000000   45.121739   84.500000   80.000000        1.523333
std     52.971691   33.426050   48.641546   46.043458        1.664107
min      1.000000    1.000000    1.000000    1.000000        0.820000
25%     46.500000   22.500000   42.750000   40.500000        0.865000
50%     92.000000   39.000000   84.500000   80.000000        1.000000
75%    137.500000   60.000000  126.250000  119.500000        1.415000
max    183.000000  253.000000  168.000000  159.000000       15.400000

In [139]:
dfplacement.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 183 entries, 0 to 182
Data columns (total 6 columns):
 #   Column          Non-Null Count  Dtype  
---  ------          --------------  -----  
 0   num             183 non-null    int64  
 1   university      183 non-null    object 
 2   size            115 non-null    float64
 3   bachelors       168 non-null    float64
 4   doctorate       159 non-null    float64
 5   placementscore  183 non-null    float64
dtypes: float64(4), int64(1), object(1)
memory usage: 8.7+ KB


In [157]:
dfplacement.sample(3)

num                             university   size  bachelors  doctorate  \
39    40                  University of Chicago   54.0       34.0       49.0   
0      1  Massachusetts Institute of Technology  119.0        1.0        1.0   
100  101            University of South Florida   13.0      126.0       89.0   

     placementscore  
39             1.47  
0             15.40  
100            0.94

In [141]:
dfbestpaper = pd.read_csv("data/best-paper.csv", delimiter='|')
dfbestpaper = dfbestpaper.applymap(lambda x: x.strip() if isinstance(x, str) else x)
dfbestpaper.describe()

Year    Coauthors
count  4815.000000  4815.000000
mean   2014.076843     5.455659
std       5.956105     3.199965
min    1996.000000     1.000000
25%    2010.000000     3.000000
50%    2015.000000     5.000000
75%    2019.000000     7.000000
max    2022.000000    26.000000

In [142]:
dfbestpaper.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 4815 entries, 0 to 4814
Data columns (total 6 columns):
 #   Column      Non-Null Count  Dtype 
---  ------      --------------  ----- 
 0   Author      4815 non-null   object
 1   University  4815 non-null   object
 2   Conference  4815 non-null   object
 3   Area        4815 non-null   object
 4   Year        4815 non-null   int64 
 5   Coauthors   4815 non-null   int64 
dtypes: int64(2), object(4)
memory usage: 225.8+ KB


In [158]:
dfbestpaper.sample(3)

Author                     University Conference  \
2490  Christian Sandvig         University of Michigan        CHI   
4514     Yonatan Wexler  Weizmann Institute of Science       ICCV   
3603      Anindya Ghose            New York University        WWW   

                            Area  Year  Coauthors  
2490  Human-Computer Interaction  2015          8  
4514             Computer Vision  2003          3  
3603              World Wide Web  2011          3

In [148]:
dfpreference = pd.read_csv("data/preferences.csv")
dfpreference.describe()

preference
count   99.000000
mean     2.747475
std      1.311981
min      1.000000
25%      2.000000
50%      3.000000
75%      4.000000
max      5.000000

In [149]:
dfpreference.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 99 entries, 0 to 98
Data columns (total 2 columns):
 #   Column      Non-Null Count  Dtype 
---  ------      --------------  ----- 
 0   conference  99 non-null     object
 1   preference  99 non-null     int64 
dtypes: int64(1), object(1)
memory usage: 1.7+ KB


In [164]:
dfpreference.sample(3)

conference  preference
63     emsoft           1
12       eccv           3
55     asplos           2

In [104]:
university_alias = {}
with open('data/universities.csv', 'r') as file:
    for line in file:
        unis = line.split(',')
        unis.pop()
        first = unis.pop(0)
        university_alias[first] = unis 
count = 5
for k, v in university_alias.items():
    if count < 0:
        break
    count -= 1
    print(f"{k} {v}")
print(len(university_alias))

University of Kentucky []
Colorado State University []
University of Illinois at Chicago []
Duke University []
Florida International University []
UCCS []
186


In [106]:
def get_alias(uni):
    if uni in university_alias:
        return uni
    for k, v in university_alias.items():
        if uni in v:
            return k
    return None 

# Methodology

I want to do a little better than following the rankings blindly, here are the factors I want to consider.

## Data

1. Professor Conference Score (essentially the csrankings.org score)
2. Best Paper Awards
3. Placement Rank (taken from the drafty placement rank, which is pagerank on professors original universities and then employment universities)
4. Variance of Professors

## Method

### Professor Score
A professor will be given a score based on their conference score and best papers. 

Both will have weights by:
- Will be weighted by logarithmically by the year published (the older, the less score)
- Will be weighted by how interested I am in the area (weights defined manually)

### Meta Scores

#### Placement Rank
A Placement Rank will be computed based on the professor score (the places where more important professors originate from matters more).

Logarithmic scale will be used to normalize the professor scores here.

#### Professor Score Variance
Variance of professor score will then be computed

#### Professor Score Sum
A sum of professors score will then be computed

### Final Score

I will take the Meta Scores, normalize them with min max scaling. Then I will apply some weights and get my results.



# Computing Professor Scores

- I will use the `generated-author-info` dataset for each professors to give their scores for each unique year-conference combination
- I will use the `best-paper` dataset for each professor to give a bonus for each professor with a best paper
- I will use `preference` dataset (which I manually created) to give weight preferences.


In [197]:
def year_weight(year):
    # 1970 - 2023
    year = 2023 - year + 2
    year *= 0.5
    return math.log(year)
[year_weight(i) * 0.333 for i in range(1970, 2024)]

[1.103623939555951,
 1.0975136763794417,
 1.0912891960863949,
 1.0849461471611537,
 1.0784799245707386,
 1.0718856496811109,
 1.065158148144377,
 1.058291925505866,
 1.0512811402429878,
 1.044119573904407,
 1.0368005979670547,
 1.0293171369683194,
 1.0216616273994945,
 1.0138259717618998,
 1.0058014870860728,
 0.997578847093479,
 0.9891480170347104,
 0.9804981800624246,
 0.971617653784065,
 0.9624937953794228,
 0.9531128933495131,
 0.94346004357072,
 0.9335190068418762,
 0.9232720445058472,
 0.912699727967092,
 0.901780716967036,
 0.8904915002590341,
 0.8788060907618811,
 0.8666956652529798,
 0.8541281360346917,
 0.8410676385546492,
 0.8274739143794042,
 0.8133015627779451,
 0.7984991258418574,
 0.7830079606354381,
 0.7667608359670173,
 0.749680168935963,
 0.7316757842529612,
 0.7126420324442582,
 0.6924540333793854,
 0.6709627058405742,
 0.6479880796354194,
 0.6233101249082299,
 0.5966559032529424,
 0.5676811147153956,
 0.5359428248405554,
 0.5008577731264994,
 0.4616360222529236,
 0.

In [199]:
def area_weight(area):
    # score of 1-5
    area_score = dfpreference[dfpreference['conference'] == area]['preference'].values[0]
    return math.log(area_score + 1, 8)
[math.log(i+1, math.e ** 0.125)*0.125 for i in range(1,6)]

[0.6931471805599453,
 1.0986122886681098,
 1.3862943611198906,
 1.6094379124341003,
 1.791759469228055]

In [200]:
dfauthorscore = pd.DataFrame(columns=['name', 'university', 'score'])

for index, row in tqdm(dfcsrankings.iterrows(), desc="Prof Scores", unit="item", total=len(dfcsrankings)):
    name = row['name']
    university = row['dept']

    year = row['year']
    area = row['area']

    yearweight = year_weight(year)
    areaweight = area_weight(area)


    count = row['adjustedcount'] * yearweight * areaweight

    existing_rows = dfauthorscore[dfauthorscore['name'] == name]
    if existing_rows.empty:
        dfauthorscore.loc[len(dfauthorscore)] = [name, university, count]
    else:
        for idx in existing_rows.index:
            dfauthorscore.at[idx, 'score'] += count

Prof Scores:   0%|                                                                                                                                                                                                           | 0/199906 [00:00<?, ?item/s]

Prof Scores:   0%|                                                                                                                                                                                                 | 16/199906 [00:00<20:57, 158.94item/s]

Prof Scores:   0%|                                                                                                                                                                                                 | 56/199906 [00:00<11:11, 297.46item/s]

Prof Scores:   0%|                                                                                                                                                                                                | 100/199906 [00:00<09:15, 359.77item/s]

Prof Scores:   0%|▏                                                                                                                                                                                               | 141/199906 [00:00<08:48, 377.79item/s]

...

Prof Scores: 100%|████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▉| 199833/199906 [14:02<00:00, 168.69item/s]

Prof Scores: 100%|████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▉| 199852/199906 [14:02<00:00, 174.09item/s]

Prof Scores: 100%|████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▉| 199870/199906 [14:02<00:00, 174.70item/s]

Prof Scores: 100%|████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▉| 199888/199906 [14:02<00:00, 166.83item/s]

Prof Scores: 100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 199906/199906 [14:03<00:00, 237.13item/s]

In [212]:
dfpaperscore = pd.DataFrame(columns=['name', 'university', 'score'])

for index, row in tqdm(dfbestpaper.iterrows(), desc="Best Paper Scores", unit="item", total=len(dfbestpaper)):
    name = row['Author']
    university = row['University']

    year = row['Year']
    area = row['Area']
    coauthors = 1.0 / float(row['Coauthors'])

    yearweight = year_weight(year)
    areaweight = area_weight(area)

    count = 10 * yearweight * areaweight * coauthors

    existing_rows = dfpaperscore[dfpaperscore['name'] == name]
    if existing_rows.empty:
        dfpaperscore.loc[len(dfpaperscore)] = [name, university, count]
    else:
        for idx in existing_rows.index:
            dfpaperscore.at[idx, 'score'] += count

Best Paper Scores:   0%|                                                                                                           | 0/4815 [00:00<?, ?item/s]

Best Paper Scores:   0%|▎                                                                                                | 18/4815 [00:00<00:27, 173.63item/s]

Best Paper Scores:   1%|▋                                                                                                | 37/4815 [00:00<00:26, 182.98item/s]

Best Paper Scores:   1%|█▏                                                                                               | 56/4815 [00:00<00:25, 184.38item/s]

Best Paper Scores:   2%|█▌                                                                                               | 75/4815 [00:00<00:25, 183.85item/s]

...

Best Paper Scores:  99%|█████████████████████████████████████████████████████████████████████████████████████████████▊ | 4754/4815 [00:26<00:00, 172.34item/s]

Best Paper Scores:  99%|██████████████████████████████████████████████████████████████████████████████████████████████▏| 4772/4815 [00:26<00:00, 168.43item/s]

Best Paper Scores: 100%|██████████████████████████████████████████████████████████████████████████████████████████████▌| 4791/4815 [00:26<00:00, 173.86item/s]

Best Paper Scores: 100%|██████████████████████████████████████████████████████████████████████████████████████████████▉| 4809/4815 [00:26<00:00, 171.50item/s]

Best Paper Scores: 100%|███████████████████████████████████████████████████████████████████████████████████████████████| 4815/4815 [00:26<00:00, 181.74item/s]

In [202]:
dfauthorscore.describe()

score
count  16202.000000
mean       4.940152
std        8.031824
min        0.000000
25%        0.740061
50%        2.072810
75%        5.595020
max      105.267098

In [203]:
dfauthorscore.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 16202 entries, 0 to 16201
Data columns (total 3 columns):
 #   Column      Non-Null Count  Dtype  
---  ------      --------------  -----  
 0   name        16202 non-null  object 
 1   university  16202 non-null  object 
 2   score       16202 non-null  float64
dtypes: float64(1), object(2)
memory usage: 1022.4+ KB


In [206]:
dfauthorscore.sample(3)

name                           university      score
8136  Liang Wang 0001          Chinese Academy of Sciences  13.173406
1472        Ben Leong     National University of Singapore   1.832100
6841  John R. Gilbert  Univ. of California - Santa Barbara   3.033604

In [213]:
dfpaperscore.describe()

score
count  4099.000000
mean      3.421484
std       4.069683
min       0.128361
25%       1.213362
50%       2.159991
75%       3.788329
max      47.309503

In [215]:
dfpaperscore.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 4099 entries, 0 to 4098
Data columns (total 3 columns):
 #   Column      Non-Null Count  Dtype  
---  ------      --------------  -----  
 0   name        4099 non-null   object 
 1   university  4099 non-null   object 
 2   score       4099 non-null   float64
dtypes: float64(1), object(2)
memory usage: 128.1+ KB


In [218]:
dfpaperscore.sample(3)

name                                     university     score
2137   Ratul Mahajan                                      Microsoft  2.328240
1248     Hanru Jiang  University of Science and Technology of China  1.160840
3239  Michael D. Day                                            IBM  1.732763

In [219]:
dfscore = dfauthorscore.copy()
for index, row in tqdm(dfpaperscore.iterrows(), desc="Merge Scores", unit="item", total=len(dfpaperscore)):
    name = row['name']
    university = row['university']
    count = row['score']

    existing_rows = dfscore[dfscore['name'] == name]

    if existing_rows.empty:
        dfscore.loc[len(dfscore)] = [name, university, count]
    else:
        for idx in existing_rows.index:
            dfscore.at[idx, 'score'] += count

Merge Scores:   0%|                                                                                                                | 0/4099 [00:00<?, ?item/s]

Merge Scores:   0%|▎                                                                                                     | 12/4099 [00:00<00:34, 116.92item/s]

Merge Scores:   1%|▌                                                                                                     | 25/4099 [00:00<00:33, 121.17item/s]

Merge Scores:   1%|▉                                                                                                     | 38/4099 [00:00<00:35, 113.47item/s]

Merge Scores:   1%|█▎                                                                                                    | 51/4099 [00:00<00:34, 117.71item/s]

...

Merge Scores:  99%|██████████████████████████████████████████████████████████████████████████████████████████████████▉ | 4056/4099 [00:36<00:00, 106.11item/s]

Merge Scores:  99%|███████████████████████████████████████████████████████████████████████████████████████████████████▏| 4068/4099 [00:36<00:00, 108.90item/s]

Merge Scores: 100%|███████████████████████████████████████████████████████████████████████████████████████████████████▌| 4079/4099 [00:36<00:00, 105.23item/s]

Merge Scores: 100%|███████████████████████████████████████████████████████████████████████████████████████████████████▊| 4090/4099 [00:36<00:00, 105.78item/s]

Merge Scores: 100%|████████████████████████████████████████████████████████████████████████████████████████████████████| 4099/4099 [00:36<00:00, 112.23item/s]

In [220]:
dfscore['university'] = dfscore['university'].apply(get_alias)
dfscore = dfscore.dropna(subset=['university'])
dfscore.describe()

score
count  7493.000000
mean      6.454446
std       9.560197
min       0.000000
25%       1.192176
50%       2.986266
75%       7.698629
max     111.268106

In [221]:
dfscore.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 7493 entries, 4 to 19418
Data columns (total 3 columns):
 #   Column      Non-Null Count  Dtype  
---  ------      --------------  -----  
 0   name        7493 non-null   object 
 1   university  7493 non-null   object 
 2   score       7493 non-null   float64
dtypes: float64(1), object(2)
memory usage: 234.2+ KB


In [222]:
dfscore.sample(3)

name                             university     score
12738  Shobha Vasudevan  Univ. of Illinois at Urbana-Champaign  1.337812
3423     Ding Yuan 0004                  University of Toronto  3.809756
16624     Adam S. Miner                    Stanford University  1.072959

# Computing Professor Placement Scores

I will compute three scores, one for relationship between bachelor with placement, bachelor with phd, and phd with placement.

I will do this by mapping dfcsprofs onto dfscore, which will let me value each one of the connections.

In [224]:
dfscoreplacement = dfscore.copy()
dfscoreplacement['name'] = dfscoreplacement['name'].str.lower()
dfcsprofsplacement = dfcsprofs.copy()
dfcsprofsplacement['name'] = dfcsprofsplacement['FullName'].str.lower()
dfcsprofsplacement['university'] = dfcsprofsplacement['University'].apply(get_alias)
dfcsprofsplacement['bachelors'] = dfcsprofsplacement['Bachelors'].apply(get_alias)
dfcsprofsplacement['doctorate'] = dfcsprofsplacement['Doctorate'].apply(get_alias)
dfcsprofsplacement.dropna(subset=['university'])
dfcsprofsplacement.dropna(subset=['bachelors'])
dfcsprofsplacement.dropna(subset=['doctorate'])

mapping_dict = dict(zip(dfcsprofsplacement['name'], zip(dfcsprofsplacement['university'],
                                                        dfcsprofsplacement['bachelors'],
                                                        dfcsprofsplacement['doctorate'])))
dfscoreplacement[['placement', 'bachelors', 'doctorate']] = dfscoreplacement['name'].map(mapping_dict).apply(pd.Series)

dfscoreplacement = dfscoreplacement.dropna(subset=['placement', 'bachelors', 'doctorate'])
dfscoreplacement.describe()

score
count  864.000000
mean     9.378363
std     10.774190
min      0.027031
25%      2.451700
50%      5.282484
75%     12.848515
max     73.308460

In [225]:
dfscoreplacement.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 864 entries, 30 to 19109
Data columns (total 6 columns):
 #   Column      Non-Null Count  Dtype  
---  ------      --------------  -----  
 0   name        864 non-null    object 
 1   university  864 non-null    object 
 2   score       864 non-null    float64
 3   placement   864 non-null    object 
 4   bachelors   864 non-null    object 
 5   doctorate   864 non-null    object 
dtypes: float64(1), object(5)
memory usage: 47.2+ KB


In [227]:
dfscoreplacement.sample(3)

name                          university      score  \
2470  christopher d. carothers    Rensselaer Polytechnic Institute   0.463978   
5982           james c. lester     North Carolina State University   8.728414   
261               alan h. barr  California Institute of Technology  13.763033   

                               placement                         bachelors  \
2470    Rensselaer Polytechnic Institute   Georgia Institute of Technology   
5982     North Carolina State University     University of Texas at Austin   
261   California Institute of Technology  Rensselaer Polytechnic Institute   

                             doctorate  
2470   Georgia Institute of Technology  
5982     University of Texas at Austin  
261   Rensselaer Polytechnic Institute